In [21]:
import numpy as np
import pandas as pd
import os
import urllib
import tarfile
from sklearn.model_selection import StratifiedShuffleSplit as SSS
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.svm import SVR
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV
import joblib
from scipy.stats import expon, reciprocal

In [2]:
DOWNLOAD_ROOT = "https://raw.githubusercontent.com/ageron/handson-ml2/master/"
HOUSING_PATH = os.path.join("datasets", "housing")
HOUSING_URL = DOWNLOAD_ROOT + "datasets/housing/housing.tgz"

In [3]:
def fetch_housing_data(housing_url=HOUSING_URL, housing_path=HOUSING_PATH):
    os.makedirs(housing_path, exist_ok = True) # Create directory if not already there
    tgz_path = os.path.join(housing_path, 'housing.tgz') # Make path for our tgz file
    urllib.request.urlretrieve(housing_url, tgz_path) # Download the file
    housing_tgz = tarfile.open(tgz_path) # Open the file
    housing_tgz.extractall(path=housing_path) # Extract from tarfile
    housing_tgz.close()

In [4]:
fetch_housing_data()

In [5]:
def load_housing_data(housing_path=HOUSING_PATH):
    csv_path = os.path.join(housing_path, 'housing.csv')
    return pd.read_csv(csv_path)

In [6]:
housing = load_housing_data()
housing.head()

longitude  latitude  housing_median_age  total_rooms  total_bedrooms  \
0    -122.23     37.88                41.0        880.0           129.0   
1    -122.22     37.86                21.0       7099.0          1106.0   
2    -122.24     37.85                52.0       1467.0           190.0   
3    -122.25     37.85                52.0       1274.0           235.0   
4    -122.25     37.85                52.0       1627.0           280.0   

   population  households  median_income  median_house_value ocean_proximity  
0       322.0       126.0         8.3252            452600.0        NEAR BAY  
1      2401.0      1138.0         8.3014            358500.0        NEAR BAY  
2       496.0       177.0         7.2574            352100.0        NEAR BAY  
3       558.0       219.0         5.6431            341300.0        NEAR BAY  
4       565.0       259.0         3.8462            342200.0        NEAR BAY

In [7]:
# Now we want to do some stratified sampling based on median_income which seems to be fairly important

housing['income_cat'] = pd.cut(housing['median_income'], # Chopping up median income because it's important
                              bins=[0., 1.5, 3.0, 4.5, 6., np.inf], # Chop into categories of 0 to 1.5, 1.5 to 3, etc
                              labels=[1,2,3,4,5]) # Generic labels

split = SSS(n_splits=1, test_size=0.2, random_state=42) # Initialize our split with proper test size/random state to match book
for train_index, test_index in split.split(housing, housing['income_cat']):
    strat_train_set = housing.loc[train_index]
    strat_test_set = housing.loc[test_index]

In [8]:
# Now that we finished with our income_cat feature we can drop it

for set_ in (strat_train_set, strat_test_set):
    set_.drop('income_cat', axis=1, inplace=True)

In [9]:
housing = strat_train_set.drop('median_house_value', axis=1)
housing_labels = strat_train_set['median_house_value'].copy()

In [10]:
from sklearn.base import BaseEstimator, TransformerMixin

# column index
rooms_ix, bedrooms_ix, population_ix, households_ix = 3, 4, 5, 6

class CombinedAttributesAdder(BaseEstimator, TransformerMixin):
    def __init__(self, add_bedrooms_per_room = True): # no *args or **kargs
        self.add_bedrooms_per_room = add_bedrooms_per_room
    def fit(self, X, y=None):
        return self  # nothing else to do
    def transform(self, X):
        rooms_per_household = X[:, rooms_ix] / X[:, households_ix]
        population_per_household = X[:, population_ix] / X[:, households_ix]
        if self.add_bedrooms_per_room:
            bedrooms_per_room = X[:, bedrooms_ix] / X[:, rooms_ix]
            return np.c_[X, rooms_per_household, population_per_household,
                         bedrooms_per_room]
        else:
            return np.c_[X, rooms_per_household, population_per_household]

attr_adder = CombinedAttributesAdder(add_bedrooms_per_room=False)
housing_extra_attribs = attr_adder.transform(housing.values)

In [11]:
# Setup a pipeline to do all we've done already for numerical features
# Note that all estimators but the last must be transformers(specifically they must have a
# fit_transform() method)

num_pipeline = Pipeline([
    ('imputer', SimpleImputer(strategy='median')),
    ('attribs_adder', CombinedAttributesAdder()), 
    ('std_scaler', StandardScaler())
]) 

In [12]:
housing_num = housing.drop('ocean_proximity', axis=1) # Drop non numerical feature for imputation
housing_cat = housing[['ocean_proximity']] # doubles brackets to get a dataframe instead of a series

In [29]:
# Our previous pipeline applies to all columns in a dataframe. To deal with both our categorical and
# numerical features at once we use ColumnTransformer to perform our pipeline only on numerical features
# and OneHotEncoder only on categorical features

num_attribs = list(housing_num)
cat_attribs = ['ocean_proximity']

full_pipeline = ColumnTransformer([
    ('num', num_pipeline, num_attribs), 
    ('cat', OneHotEncoder(), cat_attribs)
])

housing_prepared = full_pipeline.fit_transform(housing)

**Exercise One**

Try with an SVM!

In [18]:
# Simple Support Vector Machine

SVR_model = SVR()
SVR_model.fit(housing_prepared, housing_labels)

c:\users\tsb\appdata\local\programs\python\python37\lib\site-packages\sklearn\svm\base.py:193: FutureWarning: The default value of gamma will change from 'auto' to 'scale' in version 0.22 to account better for unscaled features. Set gamma explicitly to 'auto' or 'scale' to avoid this warning.
  "avoid this warning.", FutureWarning)


SVR(C=1.0, cache_size=200, coef0=0.0, degree=3, epsilon=0.1,
    gamma='auto_deprecated', kernel='rbf', max_iter=-1, shrinking=True,
    tol=0.001, verbose=False)

In [15]:
SVR_pred = SVR_model.predict(housing_prepared)
SVR_mse = mean_squared_error(SVR_pred, housing_labels)
SVR_rmse = np.sqrt (SVR_mse)
SVR_rmse

118577.43356412371

In [60]:
# Our rmse was terrible, worse than either linear regression or random forests
# Lets try to fine tune our hyper parameters

param_grid = [
    {'kernel': ['linear', 'rbf'], 'C': [10., 30., 100., 300., 1000., 3000.],
    'gamma': [0.01, 0.03, 0.1, 0.3, 1.0, 3.0]}
]

SVR_model = SVR()

grid_search = GridSearchCV(SVR_model, param_grid, cv=5,
                          scoring='neg_mean_squared_error',
                          return_train_score=True, 
                          verbose=2, 
                          n_jobs=-1)

grid_search.fit(housing_prepared, housing_labels)

Fitting 5 folds for each of 72 candidates, totalling 360 fits
[CV] C=10.0, gamma=0.01, kernel=linear ...............................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


[CV] ................ C=10.0, gamma=0.01, kernel=linear, total=   4.4s
[CV] C=10.0, gamma=0.01, kernel=linear ...............................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    6.1s remaining:    0.0s


[CV] ................ C=10.0, gamma=0.01, kernel=linear, total=   4.3s
[CV] C=10.0, gamma=0.01, kernel=linear ...............................
[CV] ................ C=10.0, gamma=0.01, kernel=linear, total=   4.4s
[CV] C=10.0, gamma=0.01, kernel=linear ...............................
[CV] ................ C=10.0, gamma=0.01, kernel=linear, total=   4.3s
[CV] C=10.0, gamma=0.01, kernel=linear ...............................
[CV] ................ C=10.0, gamma=0.01, kernel=linear, total=   4.4s
[CV] C=10.0, gamma=0.01, kernel=rbf ..................................
[CV] ................... C=10.0, gamma=0.01, kernel=rbf, total=   7.4s
[CV] C=10.0, gamma=0.01, kernel=rbf ..................................
[CV] ................... C=10.0, gamma=0.01, kernel=rbf, total=   7.4s
[CV] C=10.0, gamma=0.01, kernel=rbf ..................................
[CV] ................... C=10.0, gamma=0.01, kernel=rbf, total=   7.4s
[CV] C=10.0, gamma=0.01, kernel=rbf ..................................
[CV] .

...

[CV] ................ C=300.0, gamma=3.0, kernel=linear, total=   4.4s
[CV] C=300.0, gamma=3.0, kernel=linear ...............................
[CV] ................ C=300.0, gamma=3.0, kernel=linear, total=   4.3s
[CV] C=300.0, gamma=3.0, kernel=rbf ..................................
[CV] ................... C=300.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=300.0, gamma=3.0, kernel=rbf ..................................
[CV] ................... C=300.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=300.0, gamma=3.0, kernel=rbf ..................................
[CV] ................... C=300.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=300.0, gamma=3.0, kernel=rbf ..................................
[CV] ................... C=300.0, gamma=3.0, kernel=rbf, total=   7.7s
[CV] C=300.0, gamma=3.0, kernel=rbf ..................................
[CV] ................... C=300.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=1000.0, gamma=0.01, kernel=linear .............................
[CV] .

[CV] ............... C=1000.0, gamma=3.0, kernel=linear, total=   4.6s
[CV] C=1000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=1000.0, gamma=3.0, kernel=linear, total=   4.5s
[CV] C=1000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=1000.0, gamma=3.0, kernel=linear, total=   4.6s
[CV] C=1000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=1000.0, gamma=3.0, kernel=linear, total=   4.5s
[CV] C=1000.0, gamma=3.0, kernel=rbf .................................
[CV] .................. C=1000.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=1000.0, gamma=3.0, kernel=rbf .................................
[CV] .................. C=1000.0, gamma=3.0, kernel=rbf, total=   7.7s
[CV] C=1000.0, gamma=3.0, kernel=rbf .................................
[CV] .................. C=1000.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=1000.0, gamma=3.0, kernel=rbf .................................
[CV] .

[CV] .................. C=3000.0, gamma=1.0, kernel=rbf, total=   6.9s
[CV] C=3000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=3000.0, gamma=3.0, kernel=linear, total=   4.8s
[CV] C=3000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=3000.0, gamma=3.0, kernel=linear, total=   4.8s
[CV] C=3000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=3000.0, gamma=3.0, kernel=linear, total=   5.0s
[CV] C=3000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=3000.0, gamma=3.0, kernel=linear, total=   4.9s
[CV] C=3000.0, gamma=3.0, kernel=linear ..............................
[CV] ............... C=3000.0, gamma=3.0, kernel=linear, total=   4.8s
[CV] C=3000.0, gamma=3.0, kernel=rbf .................................
[CV] .................. C=3000.0, gamma=3.0, kernel=rbf, total=   7.6s
[CV] C=3000.0, gamma=3.0, kernel=rbf .................................
[CV] .

[Parallel(n_jobs=1)]: Done 360 out of 360 | elapsed: 51.4min finished


GridSearchCV(cv=5, error_score='raise-deprecating',
             estimator=SVR(C=1.0, cache_size=200, coef0=0.0, degree=3,
                           epsilon=0.1, gamma='auto_deprecated', kernel='rbf',
                           max_iter=-1, shrinking=True, tol=0.001,
                           verbose=False),
             iid='warn', n_jobs=None,
             param_grid=[{'C': [10.0, 30.0, 100.0, 300.0, 1000.0, 3000.0],
                          'gamma': [0.01, 0.03, 0.1, 0.3, 1.0, 3.0],
                          'kernel': ['linear', 'rbf']}],
             pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
             scoring='neg_mean_squared_error', verbose=2)

In [16]:
grid_search.best_params_

NameError: name 'grid_search' is not defined

In [ ]:
grid_search.best_estimator_

In [66]:
neg_mse = grid_search.best_score_
mse = -neg_mse
rmse = np.sqrt(mse)
print(mse)
print(rmse)

4237489445.3787646
65096.0017618499


In [70]:
# Still not great, but much better than before

SVR_model = grid_search.best_estimator_
joblib.dump(SVR_model, 'models/SVR_model.pkl')

['models/SVR_model.pkl']

**Exercise 2**

Replace Grid Search with a Random Search

In [43]:
param_distributions = {
    'kernel': ['linear', 'rbf'], 
    'C': reciprocal(20,200000),
    'gamma': expon(scale=1.0)
}


SVR_model = SVR()

rnd_search = RandomizedSearchCV(SVR_model, 
                           param_distributions=param_distributions, 
                           n_iter=50,
                           cv=5,
                           scoring='neg_mean_squared_error',
                           verbose=2, 
                           n_jobs=-1, 
                           )

rnd_search.fit(housing_prepared, housing_labels)

Fitting 5 folds for each of 5 candidates, totalling 25 fits


[Parallel(n_jobs=-1)]: Using backend LokyBackend with 8 concurrent workers.
[Parallel(n_jobs=-1)]: Done  23 out of  25 | elapsed:  2.6min remaining:   13.7s
[Parallel(n_jobs=-1)]: Done  25 out of  25 | elapsed:  2.7min finished


RandomizedSearchCV(cv=5, error_score='raise-deprecating',
                   estimator=SVR(C=1.0, cache_size=200, coef0=0.0, degree=3,
                                 epsilon=0.1, gamma='auto_deprecated',
                                 kernel='rbf', max_iter=-1, shrinking=True,
                                 tol=0.001, verbose=False),
                   iid='warn', n_iter=5, n_jobs=-1,
                   param_distributions={'C': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000176D38577C8>,
                                        'gamma': <scipy.stats._distn_infrastructure.rv_frozen object at 0x00000176D3857A48>,
                                        'kernel': ['linear', 'rbf']},
                   pre_dispatch='2*n_jobs', random_state=None, refit=True,
                   return_train_score=False, scoring='neg_mean_squared_error',
                   verbose=2)

In [45]:
neg_mse = rnd_search.best_score_
mse = -neg_mse
rmse = np.sqrt(mse)
print(mse)
print(rmse) # Even better than the grid search!

3776176391.944553
61450.601233385445


In [ ]:
SVR_model = rnd_search.best_estimator_
joblib.dump(SVR_model, 'models/SVR_tuned_model.pkl')

**Exercise 3**

Add transformer to preperation pipeline which chooses only most important attributes

In [24]:
# Have to find feature importances somehow, so we create a random forest model and inspect that

forest_reg = RandomForestRegressor()
forest_reg.fit(housing_prepared, housing_labels)
feature_importances = forest_reg.feature_importances_

c:\users\tsb\appdata\local\programs\python\python37\lib\site-packages\sklearn\ensemble\forest.py:245: FutureWarning: The default value of n_estimators will change from 10 in version 0.20 to 100 in 0.22.
  "10 in version 0.20 to 100 in 0.22.", FutureWarning)


In [31]:
from sklearn.base import BaseEstimator, TransformerMixin

def indices_of_top_k(arr, k):
    return np.sort(np.argpartition(np.array(arr), -k)[-k:])

class TopFeatureSelector(BaseEstimator, TransformerMixin):
    def __init__(self, feature_importances, k): # Need our array of feature importance rankings and the number we'd like to keep
        self.feature_importances = feature_importances
        self.k = k
    def fit(self, X, y=None):
        self.feature_indices_ = indices_of_top_k(self.feature_importances, self.k)
        return self
    def transform(self, X):
        return X[:, self.feature_indices_]

In [32]:
k=5

In [36]:
# Check that it's working

selector = TopFeatureSelector(feature_importances, k)
selector.fit(housing_prepared)
selector.transform(housing_prepared)

array([[-1.15604281,  0.77194962, -0.61493744, -0.08649871,  0.        ],
       [-1.17602483,  0.6596948 ,  1.33645936, -0.03353391,  0.        ],
       [ 1.18684903, -1.34218285, -0.5320456 , -0.09240499,  0.        ],
       ...,
       [ 1.58648943, -0.72478134, -0.3167053 , -0.03055414,  1.        ],
       [ 0.78221312, -0.85106801,  0.09812139,  0.06150916,  0.        ],
       [-1.43579109,  0.99645926, -0.15779865, -0.09586294,  0.        ]])

In [33]:
prep_and_select_pipeline = Pipeline([
    ('preperation', full_pipeline),
    ('feature_selection', TopFeatureSelector(feature_importances, k))
])

In [37]:
housing_prepared_top_features = prep_and_select_pipeline.fit_transform(housing)

In [38]:
housing_prepared_top_features[0:5]

array([[-1.15604281,  0.77194962, -0.61493744, -0.08649871,  0.        ],
       [-1.17602483,  0.6596948 ,  1.33645936, -0.03353391,  0.        ],
       [ 1.18684903, -1.34218285, -0.5320456 , -0.09240499,  0.        ],
       [-0.01706767,  0.31357576, -1.04556555,  0.08973561,  1.        ],
       [ 0.49247384, -0.65929936, -0.44143679, -0.00419445,  0.        ]])

**Exercise 4**

Create pipeline for data prep and prediction

In [50]:
prep_select_and_predict_pipeline = Pipeline([
    ('preperation', full_pipeline),
    ('feature_selection', TopFeatureSelector(feature_importances, k)),
    ('svm_reg', SVR(**rnd_search.best_params_))
])

In [52]:
prep_select_and_predict_pipeline.fit(housing, housing_labels)

Pipeline(memory=None,
         steps=[('preperation',
                 ColumnTransformer(n_jobs=None, remainder='drop',
                                   sparse_threshold=0.3,
                                   transformer_weights=None,
                                   transformers=[('num',
                                                  Pipeline(memory=None,
                                                           steps=[('imputer',
                                                                   SimpleImputer(add_indicator=False,
                                                                                 copy=True,
                                                                                 fill_value=None,
                                                                                 missing_values=nan,
                                                                                 strategy='median',
                                                              

In [53]:
prep_select_and_predict_pipeline.predict(housing.iloc[:4])

array([199258.41244986, 357693.77258301, 170734.84525309,  46270.46533462])

In [54]:
housing_labels.iloc[:4]

17606    286600.0
18632    340600.0
14650    196900.0
3230      46300.0
Name: median_house_value, dtype: float64